In [1]:
from datetime import datetime
import cv2
import pytesseract

In [2]:
def extract_timestamp(frame, x, y, w, h):
    CONFIG = r"--psm 6 -c tessedit_char_whitelist=0123456789:"
    gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
    thresh = cv2.threshold(gray, 150, 255, cv2.THRESH_BINARY_INV + cv2.THRESH_OTSU)[1]
    roi = thresh[y : y + h, x : x + w]
    # Show the extracted ROI
    cv2.imshow("ROI", roi)

    text = pytesseract.image_to_string(roi, config=CONFIG)
    # keep only digits and colons
    text = text.strip()
    # only keep 12 characters, e.g. 00:00:00.000
    text = text[:12]

    # parse the timestamp text to a datetime object
    try:
        timestamp = datetime.strptime(text, "%H:%M:%S:%f")
        return timestamp
    except ValueError:
        print(f"Invalid timestamp: {text}")
        return None

In [3]:
# Keyboard controls for navigation
def main_loop(
    video,
    ocr_out,
    x,
    y,
    w,
    h,
    start_frame_idx=0,
):
    frame_idx = start_frame_idx

    while video.isOpened():
        # Set the video frame index based on the current position
        video.set(cv2.CAP_PROP_POS_FRAMES, frame_idx)

        # Read the main frame
        ret, frame = video.read()
        if not ret:
            break

        # Extract the timestamp from the main frame
        # main_ocr_timestamp = extract_timestamp(frame, 1250, 900, 800, 150)
        ocr_timestamp = extract_timestamp(frame, x, y, w, h)

        # Extract the timestamp from the secondary frame
        # secondary_ocr_timestamp = extract_timestamp(sub_frame, 1850, 900, 800, 150)

        # Print the timestamps
        print("Frame timestamp:", ocr_timestamp)

        # write the frame index, main frame timestamp, secondary frame timestamp, time delta
        ocr_out.write(f"{frame_idx} {ocr_timestamp}\n")

        frame_idx += 1

    video.release()

In [4]:
# Load the videos
main_video_path = "./build/macosx/arm64/debug/j101.mp4"
secondary_video_path = "./build/macosx/arm64/debug/j201.mp4"

video = cv2.VideoCapture(main_video_path)
sub_video = cv2.VideoCapture(secondary_video_path)

with open("j101_ocr.txt", "a") as ocr_file:
    main_loop(
        video,
        ocr_file,
        1250,
        900,
        800,
        150,
        0,
    )

with open("j201_ocr.txt", "a") as ocr_file:
    main_loop(
        sub_video,
        ocr_file,
        1850,
        900,
        800,
        150,
        0,
    )


Frame timestamp: 1900-01-01 16:58:13.788000
Frame timestamp: 1900-01-01 16:58:13.369000
Frame timestamp: 1900-01-01 16:58:13.888000
Frame timestamp: 1900-01-01 16:58:13.888000
Frame timestamp: 1900-01-01 16:58:13.868000
Frame timestamp: 1900-01-01 16:58:13.983000
Frame timestamp: 1900-01-01 16:58:13.988000
Frame timestamp: 1900-01-01 16:58:13.068000
Frame timestamp: 1900-01-01 16:58:14.088000
Frame timestamp: 1900-01-01 16:58:14.088000
Frame timestamp: 1900-01-01 16:58:14.085000
Frame timestamp: 1900-01-01 16:58:14.183000
Frame timestamp: 1900-01-01 16:58:14.149000
Frame timestamp: 1900-01-01 16:58:14.285000
Frame timestamp: 1900-01-01 16:58:14.283000
Frame timestamp: 1900-01-01 16:58:14.269000
Frame timestamp: 1900-01-01 16:58:14.308000
Frame timestamp: 1900-01-01 16:58:14.333000
Frame timestamp: 1900-01-01 16:58:14.388000
Frame timestamp: 1900-01-01 16:58:14.428000
Frame timestamp: 1900-01-01 16:58:14.438000
Frame timestamp: 1900-01-01 16:58:14.488000
Frame timestamp: 1900-01-01 16:5

KeyboardInterrupt: 